<div style='color: #216969;
           background-color: #EAF6F6;
           font-size: 300%;
           border-radius:15px;
           text-align:center;
           font-weight:600;
           border-style: solid;
           border-color: dark green;
           padding: 2%;
           font-family: "Cambria";'>
XGBoost Regression Model
<a class="anchor" id="1"></a> 

In [45]:
# Import NumPy and Pandas libraries

import pandas as pd  
import numpy as np  
from sklearn.model_selection import train_test_split
from xgboost import XGBClassifier
from xgboost import XGBRegressor
from sklearn.model_selection import RandomizedSearchCV

from sklearn. ensemble import RandomForestRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_absolute_error, mean_squared_error, explained_variance_score, r2_score
from sklearn.model_selection import KFold
from scipy.stats import uniform

from sklearn.model_selection import cross_val_score, cross_validate
from sklearn.model_selection import GridSearchCV

import statsmodels.api as sm
import matplotlib.pyplot as plt
from statsmodels.sandbox.regression.predstd import wls_prediction_std

# Import dataset
df = pd.read_csv('processedmath.csv')

# Make a copy of the dataframe
df_copy = df.copy()


In [46]:
dfX = df.iloc[:, 0:(len(df.columns)-4)] # Features
dfy = df.G3 # Target variable
print(dfX.shape)
print(type(dfX))
print(dfy.shape)
print(type(dfy))

(395, 32)
<class 'pandas.core.frame.DataFrame'>
(395,)
<class 'pandas.core.series.Series'>


In [47]:
# Extract the column names from the two datasets
col_names = list(dfX.columns)
col_names.append(dfy.name)
print(col_names)

['school', 'sex', 'age', 'address', 'famsize', 'Pstatus', 'Medu', 'Fedu', 'Mjob', 'Fjob', 'reason', 'guardian', 'traveltime', 'studytime', 'failures', 'schoolsup', 'famsup', 'paid', 'activities', 'nursery', 'higher', 'internet', 'romantic', 'famrel', 'freetime', 'goout', 'Dalc', 'Walc', 'health', 'absences', 'G1', 'G2', 'G3']


In [48]:
# Conversion from Pandas Dataframe to NumPy Array
X = dfX.values
y = dfy.values
print(type(X))
print(X)

<class 'numpy.ndarray'>
[[ 0  0 18 ...  6  5  6]
 [ 0  0 17 ...  4  5  5]
 [ 0  0 15 ... 10  7  8]
 ...
 [ 1  1 21 ...  3 10  8]
 [ 1  1 18 ...  0 11 12]
 [ 1  1 19 ...  5  8  9]]


In [49]:
X_train,X_test,y_train,y_test=train_test_split(X, y, test_size=0.25, random_state=2)
#X_train,X_test,y_train,y_test=train_test_split(X, y, test_size=0.25)

In [51]:
xgbR = XGBRegressor(n_estimators = 20, learning_rate = 0.1)
xgbR.fit(X_train, y_train.ravel())

test_mse_before_tune =  mean_squared_error(xgbR.predict(X_test), y_test)
train_mse_before_tune = mean_squared_error(xgbR.predict(X_train), y_train)

test_mae_before_tune = mean_absolute_error(xgbR.predict(X_test), y_test)
train_mae_before_tune = mean_absolute_error(xgbR.predict(X_train), y_train)

test_RMSE_before_tune = np.sqrt(mean_squared_error(xgbR.predict(X_test), y_test))
train_RMSE_before_tune = np.sqrt(mean_squared_error(xgbR.predict(X_train), y_train))

test_EVS_before_tune = explained_variance_score(xgbR.predict(X_test), y_test)
train_EVS_before_tune = explained_variance_score(xgbR.predict(X_train), y_train)

print('***Original Model***')
print('----Mean Squared Error----')
print('the training mean squared error is: ', train_mse_before_tune)
print('the testing mean squared error is: ', test_mse_before_tune)

print('\n----Mean Absolute Error----')
print('the training mean absolute error is: ', train_mae_before_tune)
print('the testing mean absolute error is: ', test_mae_before_tune)

print('\n----Root Mean Square Error----')
print('the training root mean squared error is: ', test_RMSE_before_tune)
print('the testing root mean squared error is: ', train_RMSE_before_tune)

print('\n----Explained Variance Score----')
print('the training explained variance score is: ', test_EVS_before_tune)
print('the testing explained variance score is: ', train_EVS_before_tune)

***Original Model***
----Mean Squared Error----
the training mean squared error is:  2.594534222621698
the testing mean squared error is:  3.586443950543177

----Mean Absolute Error----
the training mean absolute error is:  1.3694225892147704
the testing mean absolute error is:  1.5360674189046175

----Root Mean Square Error----
the training root mean squared error is:  1.8937908940913137
the testing root mean squared error is:  1.6107557923601261

----Explained Variance Score----
the training explained variance score is:  0.8343724848132921
the testing explained variance score is:  0.9416183920116871


<div style='color: #216969;
           background-color: #EAF6F6;
           font-size: 200%;
           border-radius:15px;
           text-align:center;
           font-weight:600;
           border-style: solid;
           border-color: dark green;
           padding: 1%;
           font-family: "Cambria";'>
K-Fold Cross Validation
<a class="anchor" id="1"></a> 

In [52]:
results = cross_validate(xgbR, X, y, scoring='neg_mean_squared_error', cv=5, return_train_score = True)
print('train score: ', results['train_score'])
print('test score: ', results['test_score'])

train score:  [-2.43194634 -2.56662208 -2.5436719  -2.64672987 -2.62403549]
test score:  [-5.76417453 -7.08426513 -4.4863901  -5.57538117 -5.65648791]


In [53]:
print('***Original Model***')
print('cross val training mean_squared_error is:', sum(-results['train_score'])/len(results['train_score']))
print('cross val testing mean_squared_error is:', sum(-results['test_score'])/len(results['test_score']))

***Original Model***
cross val training mean_squared_error is: 2.562601136674392
cross val testing mean_squared_error is: 5.713339766111601


<div style='color: #216969;
           background-color: #EAF6F6;
           font-size: 200%;
           border-radius:15px;
           text-align:center;
           font-weight:600;
           border-style: solid;
           border-color: dark green;
           padding: 1%;
           font-family: "Cambria";'>
(Tuning #1) Statsmodel Ordinary Least Squares
<a class="anchor" id="1"></a> 

In [54]:
#The statsmodel.api provides key summary statistics
#The lm2 model refers to statsmodel.api model
#Add a constant to the X_train dataset and rename it as X_train_sm
X_train_sm = sm.add_constant(X_train)
print(X_train_sm)
print(X_train_sm.shape)

#Create another model using statsmodel.api using the Ordinary Least Squares (OLS) method for the model
lm2 = sm.OLS(y_train, X_train_sm).fit()

lm2.summary()

[[ 1.  0.  0. ...  0.  9.  9.]
 [ 1.  0.  0. ...  2. 10. 10.]
 [ 1.  1.  1. ...  3. 14. 12.]
 ...
 [ 1.  0.  0. ...  2.  8.  6.]
 [ 1.  0.  0. ...  4. 14. 14.]
 [ 1.  0.  0. ...  0.  6.  7.]]
(296, 33)


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                      y   R-squared:                       0.837
Model:                            OLS   Adj. R-squared:                  0.818
Method:                 Least Squares   F-statistic:                     42.35
Date:                Mon, 07 Nov 2022   Prob (F-statistic):           1.39e-85
Time:                        21:13:08   Log-Likelihood:                -608.89
No. Observations:                 296   AIC:                             1284.
Df Residuals:                     263   BIC:                             1406.
Df Model:                          32                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         -0.8209      2.470     -0.332      0.740      -5.685       4.043
x1             0.6755      0.434      1.558      0.120      -0.178       1.529
x2             0.0347      0.284      0.122      0.903      -0.525       0.595
x3            -0.2335      0.119     -1.965      0.051      -0.468       0.001
x4             0.0361      0.345      0.105      0.917      -0.643       0.715
x5            -0.1970      0.283     -0.697      0.486      -0.754       0.360
x6             0.0669      0.395      0.169      0.866      -0.712       0.846
x7             0.1236      0.150      0.822      0.412      -0.172       0.420
x8             0.0224      0.152      0.147      0.883      -0.277       0.322
x9             0.0203      0.090      0.225      0.822      -0.158       0.198
x10            0.0461      0.103      0.447      0.655      -0.157       0.249
x11            0.1003      0.129      0.775      0.439      -0.155       0.355
x12           -0.2877      0.220     -1.305      0.193      -0.722       0.146
x13            0.1525      0.191      0.800      0.425      -0.223       0.528
x14           -0.1223      0.169     -0.724      0.469      -0.455       0.210
x15            0.2386      0.207      1.151      0.251      -0.170       0.647
x16            0.5433      0.381      1.427      0.155      -0.206       1.293
x17            0.0647      0.273      0.237      0.813      -0.472       0.602
x18            0.0567      0.274      0.207      0.836      -0.483       0.597
x19           -0.3451      0.251     -1.376      0.170      -0.839       0.149
x20           -0.4850      0.332     -1.460      0.145      -1.139       0.169
x21            0.1258      0.613      0.205      0.838      -1.082       1.333
x22           -0.0577      0.331     -0.174      0.862      -0.709       0.594
x23           -0.3177      0.265     -1.199      0.232      -0.839       0.204
x24            0.3168      0.138      2.299      0.022       0.046       0.588
x25            0.1032      0.130      0.792      0.429      -0.154       0.360
x26           -0.0074      0.132     -0.056      0.956      -0.268       0.253
x27           -0.1853      0.202     -0.918      0.359      -0.583       0.212
x28            0.1586      0.139      1.143      0.254      -0.114       0.432
x29            0.0903      0.087      1.038      0.300      -0.081       0.262
x30            0.0424      0.016      2.726      0.007       0.012       0.073
x31            0.2125      0.071      2.991      0.003       0.073       0.352
x32            0.9649      0.061     15.801      0.000       0.845       1.085
==============================================================================
Omnibus:                      129.071   Durbin-Watson:                   1.851
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              487.604
Sk

In [55]:
#Using important features (P < 0.05) to evaluate the model
dfX_new = df[['famrel', 'absences', 'G1', 'G2']]
dfy_new = df.G3
col_names = list(dfX_new.columns)
col_names.append(dfy_new.name)
print(col_names)
X = dfX_new.values
y = dfy_new.values

X_train,X_test,y_train,y_test=train_test_split(X, y.ravel(), test_size=0.25, random_state=2)
#X_train,X_test,y_train,y_test=train_test_split(X, y, test_size=0.25)

['famrel', 'absences', 'G1', 'G2', 'G3']


In [56]:
xgbR_new = XGBRegressor(n_estimators = 20, learning_rate = 0.1)
xgbR_new.fit(X_train, y_train.ravel())

print('***New Model***')
print('Training MSE is: ',  mean_squared_error(xgbR_new.predict(X_train), y_train))
print('Testing MSE is: ', mean_squared_error(xgbR_new.predict(X_test), y_test))

***New Model***
Training MSE is:  3.6651904351041913
Testing MSE is:  3.7391792226623606


<div style='color: #216969;
           background-color: #EAF6F6;
           font-size: 200%;
           border-radius:15px;
           text-align:center;
           font-weight:600;
           border-style: solid;
           border-color: dark green;
           padding: 1%;
           font-family: "Cambria";'>
Grid Search
<a class="anchor" id="1"></a> 

In [57]:
mean_squared_error(xgbR_new.predict(X_test), y_test)
xgbR_new = XGBRegressor()
param_grid = {
    "n_estimators": range (10,100),
    "learning_rate": [0.01, 0.03, 0.05, 0.09, 0.1, 0.2],
    "max_depth": [2,4,6,8]
}

gs = GridSearchCV(xgbR_new, param_grid=param_grid, scoring='neg_mean_squared_error', n_jobs=-1)
gs = gs.fit(X_train, y_train)
print(-gs.best_score_)
print(gs.best_params_)

2.9543059058966543
{'learning_rate': 0.09, 'max_depth': 2, 'n_estimators': 62}


In [64]:
xgbR_final = XGBRegressor(n_estimators = 62,
                          learning_rate = 0.09,
                          max_depth = 2)

xgbR_final.fit(X_train, y_train.ravel())

preds = xgbR_final.predict(X_test)

test_mse_after_tune =  mean_squared_error(xgbR_final.predict(X_test), y_test)
train_mse_after_tune = mean_squared_error(xgbR_final.predict(X_train), y_train)

test_mae_after_tune = mean_absolute_error(xgbR_final.predict(X_test), y_test)
train_mae_after_tune = mean_absolute_error(xgbR_final.predict(X_train), y_train)

print('***Final Model***')
print('----Mean Absolute Error----')
print('Training MAE after tuning is: ', train_mae_before_tune)
print('Testing MAE after tuning is: ', test_mae_before_tune)

print('\n----Mean Squared Error----')
print('Training MSE after tuning is: ', train_mse_after_tune)
print('Testing MSE after tuning is: ', test_mse_after_tune)

print('\n----Difference in MSE----')
print('The testing MSE has improved by ', train_mse_before_tune-train_mse_after_tune, 'after tuning.')
print('The testing MSE has improved by ', test_mse_before_tune-test_mse_after_tune, 'after tuning.')

***Final Model***
----Mean Absolute Error----
Training MAE after tuning is:  1.3694225892147704
Testing MAE after tuning is:  1.5360674189046175

----Mean Squared Error----
Training MSE after tuning is:  2.4216796033716963
Testing MSE after tuning is:  1.3089113450017726

----Difference in MSE----
The testing MSE has improved by  0.17285461925000156 after tuning.
The testing MSE has improved by  2.2775326055414045 after tuning.


<div style='color: #216969;
           background-color: #EAF6F6;
           font-size: 200%;
           border-radius:15px;
           text-align:center;
           font-weight:600;
           border-style: solid;
           border-color: dark green;
           padding: 1%;
           font-family: "Cambria";'>
K-Folds Cross Validation (Final Model)
<a class="anchor" id="1"></a> 

In [59]:
results = cross_validate(xgbR_final, X, y.ravel(), scoring='neg_mean_squared_error', cv=5, return_train_score = True)
print('train score: ', results['train_score'])
print('test score: ', results['test_score'])

train score:  [-2.06785415 -2.15221592 -2.23682383 -1.99879505 -1.79611124]
test score:  [-2.66085946 -2.36243301 -1.74940083 -3.51992089 -4.43500323]


In [60]:
print('***Final Model***')
print('cross val training mean_squared_error is:', sum(-results['train_score'])/len(results['train_score']))
print('cross val testing mean_squared_error is:', sum(-results['test_score'])/len(results['test_score']))

***Final Model***
cross val training mean_squared_error is: 2.0503600409315585
cross val testing mean_squared_error is: 2.945523483861085


<div style='color: #216969;
           background-color: #EAF6F6;
           font-size: 300%;
           border-radius:15px;
           text-align:center;
           font-weight:600;
           border-style: solid;
           border-color: dark green;
           padding: 2%;
           font-family: "Cambria";'>
Random Forest Regression Model
<a class="anchor" id="1"></a> 

In [24]:
dfX = df.iloc[:, 0:(len(df.columns)-4)] # Features
dfy = df.G3 # Target variable
print(dfX.shape)
print(type(dfX))
print(dfy.shape)
print(type(dfy))

(395, 32)
<class 'pandas.core.frame.DataFrame'>
(395,)
<class 'pandas.core.series.Series'>


In [25]:
# Extract the column names from the two datasets
col_names = list(dfX.columns)
col_names.append(dfy.name)
print(col_names)

['school', 'sex', 'age', 'address', 'famsize', 'Pstatus', 'Medu', 'Fedu', 'Mjob', 'Fjob', 'reason', 'guardian', 'traveltime', 'studytime', 'failures', 'schoolsup', 'famsup', 'paid', 'activities', 'nursery', 'higher', 'internet', 'romantic', 'famrel', 'freetime', 'goout', 'Dalc', 'Walc', 'health', 'absences', 'G1', 'G2', 'G3']


In [26]:
X_train, X_test, y_train, y_test = train_test_split(dfX, dfy, test_size=0.2, random_state = 2)
#X_train,X_test,y_train,y_test=train_test_split(X, y, test_size=0.25)

In [27]:
# Create Random Forest Model
rf_reg = RandomForestRegressor(max_depth=2, random_state=1, n_estimators=20)
# Y_train is a 1D array, use ravel() to change the shape of Y_train to (n_samples,) before feed it into fit function
rf_reg.fit(X_train, y_train.ravel()) 

RandomForestRegressor(max_depth=2, n_estimators=20, random_state=1)

In [30]:
from sklearn.metrics import mean_squared_error

test_mean_squared_error_b4Tune =  mean_squared_error(rf_reg.predict(X_test), y_test)
train_mean_squared_error_b4Tune = mean_squared_error(rf_reg.predict(X_train), y_train)

print('training accuracy (r_sq) is: ', rf_reg.score(X_train,y_train))
print('testing accuracy (r_sq) is: ', rf_reg.score(X_test,y_test))
print('the training mean squared error is: ', train_mean_squared_error_b4Tune)
print('the testing mean squared error is: ', test_mean_squared_error_b4Tune)

training accuracy (r_sq) is:  0.8245207175192641
testing accuracy (r_sq) is:  0.8317815094022667
the training mean squared error is:  3.754401883000356
the testing mean squared error is:  3.213266966530711


<div style='color: #216969;
           background-color: #EAF6F6;
           font-size: 200%;
           border-radius:15px;
           text-align:center;
           font-weight:600;
           border-style: solid;
           border-color: dark green;
           padding: 1%;
           font-family: "Cambria";'>
K-Folds Cross Validation
<a class="anchor" id="1"></a> 

In [31]:
# Evaluate the Model using K-folds Cross validation
results  = cross_validate(rf_reg, dfX, dfy.ravel(), scoring='neg_mean_squared_error', cv=5, return_train_score = True)
print('train_score: ', results['train_score'])
print('test_score: ', results['test_score'])

train_score:  [-3.56846132 -3.56102031 -3.59612707 -3.00680696 -2.98242366]
test_score:  [-4.30031829 -4.94740373 -2.6762623  -4.92206992 -5.16017311]


In [32]:
print('cross val training mean_squared_error is:', sum(-results['train_score'])/len(results['train_score']))
print('cross val testing mean_squared_error is:', sum(-results['test_score'])/len(results['test_score']))

cross val training mean_squared_error is: 3.3429678659941855
cross val testing mean_squared_error is: 4.401245469163495


<div style='color: #216969;
           background-color: #EAF6F6;
           font-size: 200%;
           border-radius:15px;
           text-align:center;
           font-weight:600;
           border-style: solid;
           border-color: dark green;
           padding: 1%;
           font-family: "Cambria";'>
(Tuning) Grid Search
<a class="anchor" id="1"></a> 

In [33]:
param_grid = {
    "n_estimators": [25, 30, 35, 40, 50, 100],
    "max_features": ['auto', 'sqrt', 'log2'],
    "max_depth": [2, 4, 10, 12, 16],
    "min_samples_split": [2, 3, 4, 5, 6, 7],
    "min_samples_leaf": [2, 4, 8, 15],
    "bootstrap": ['True', 'False']
}

gs = GridSearchCV(rf_reg, param_grid=param_grid, scoring='neg_mean_squared_error', cv=5, n_jobs=-1, verbose=10)
gs = gs.fit(X_train, y_train)
print(-gs.best_score_)
print(gs.best_params_)

Fitting 5 folds for each of 4320 candidates, totalling 21600 fits
[CV 1/5; 1/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=25
[CV 1/5; 1/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=25;, score=-3.378 total time=   0.0s
[CV 4/5; 2/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=30
[CV 4/5; 2/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=30;, score=-3.888 total time=   0.0s
[CV 2/5; 4/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=40
[CV 2/5; 4/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=40;, score=-3.979 total time=   0.0s
[CV 5/5; 5/4320] START bootstrap=True, max_depth=2, max_features=auto,

[CV 2/5; 1/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=25
[CV 2/5; 1/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=25;, score=-4.157 total time=   0.0s
[CV 1/5; 3/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=35
[CV 1/5; 3/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=35;, score=-3.376 total time=   0.0s
[CV 4/5; 4/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=40
[CV 4/5; 4/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=40;, score=-3.792 total time=   0.0s
[CV 1/5; 6/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=100
[CV 1/5

[CV 4/5; 35/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=7, n_estimators=50
[CV 4/5; 35/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=7, n_estimators=50;, score=-3.840 total time=   0.0s
[CV 5/5; 35/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=7, n_estimators=50
[CV 5/5; 35/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=7, n_estimators=50;, score=-3.529 total time=   0.0s
[CV 1/5; 36/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=7, n_estimators=100
[CV 1/5; 36/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=7, n_estimators=100;, score=-3.390 total time=   0.1s
[CV 1/5; 49/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=4, min_samples_split=4, n_estimators=25

[CV 3/5; 1/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=25
[CV 3/5; 1/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=25;, score=-4.104 total time=   0.0s
[CV 5/5; 2/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=30
[CV 5/5; 2/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=30;, score=-3.675 total time=   0.0s
[CV 3/5; 4/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=40
[CV 3/5; 4/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=40;, score=-4.124 total time=   0.0s
[CV 3/5; 6/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=100
[CV 3/5

[CV 4/5; 1/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=25
[CV 4/5; 1/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=25;, score=-3.924 total time=   0.0s
[CV 2/5; 3/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=35
[CV 2/5; 3/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=35;, score=-4.045 total time=   0.0s
[CV 4/5; 5/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=50
[CV 4/5; 5/4320] END bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=2, n_estimators=50;, score=-3.840 total time=   0.1s
[CV 2/5; 7/4320] START bootstrap=True, max_depth=2, max_features=auto, min_samples_leaf=2, min_samples_split=3, n_estimators=25
[CV 2/5;

...

[CV 1/5; 3813/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=4, min_samples_split=7, n_estimators=35;, score=-4.387 total time=   0.0s
[CV 2/5; 3813/4320] START bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=4, min_samples_split=7, n_estimators=35
[CV 2/5; 3813/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=4, min_samples_split=7, n_estimators=35;, score=-6.143 total time=   0.0s
[CV 3/5; 3813/4320] START bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=4, min_samples_split=7, n_estimators=35
[CV 3/5; 3813/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=4, min_samples_split=7, n_estimators=35;, score=-6.747 total time=   0.0s
[CV 4/5; 3813/4320] START bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=4, min_samples_split=7, n_estimators=35
[CV 4/5; 3813/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=4, min_samples_

[CV 5/5; 3836/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=8, min_samples_split=5, n_estimators=30;, score=-5.871 total time=   0.0s
[CV 1/5; 3837/4320] START bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=8, min_samples_split=5, n_estimators=35
[CV 1/5; 3837/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=8, min_samples_split=5, n_estimators=35;, score=-5.715 total time=   0.0s
[CV 2/5; 3837/4320] START bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=8, min_samples_split=5, n_estimators=35
[CV 2/5; 3837/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=8, min_samples_split=5, n_estimators=35;, score=-7.629 total time=   0.0s
[CV 3/5; 3837/4320] START bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=8, min_samples_split=5, n_estimators=35
[CV 3/5; 3837/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=8, min_samples_

[CV 3/5; 3861/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=15, min_samples_split=3, n_estimators=35;, score=-9.651 total time=   0.0s
[CV 4/5; 3861/4320] START bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=15, min_samples_split=3, n_estimators=35
[CV 4/5; 3861/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=15, min_samples_split=3, n_estimators=35;, score=-9.217 total time=   0.0s
[CV 5/5; 3869/4320] START bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=15, min_samples_split=4, n_estimators=50
[CV 5/5; 3869/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=15, min_samples_split=4, n_estimators=50;, score=-6.994 total time=   0.0s
[CV 1/5; 3870/4320] START bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=15, min_samples_split=4, n_estimators=100
[CV 1/5; 3870/4320] END bootstrap=False, max_depth=12, max_features=log2, min_samples_leaf=15, min_

[CV 2/5; 3910/4320] START bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=40
[CV 2/5; 3910/4320] END bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=40;, score=-2.601 total time=   0.1s
[CV 3/5; 3910/4320] START bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=40
[CV 3/5; 3910/4320] END bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=40;, score=-4.354 total time=   0.0s
[CV 4/5; 3910/4320] START bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=40
[CV 4/5; 3910/4320] END bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=40;, score=-2.662 total time=   0.0s
[CV 5/5; 3910/4320] START bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=2, min_sample

2.702410150875521
{'bootstrap': 'True', 'max_depth': 10, 'max_features': 'auto', 'min_samples_leaf': 8, 'min_samples_split': 2, 'n_estimators': 50}


In [35]:
rf_reg_final = RandomForestRegressor(max_depth=10,
                                     random_state=1, 
                                     n_estimators=50, 
                                     bootstrap='True', 
                                     max_features='auto', 
                                     min_samples_leaf=8, 
                                     min_samples_split=2)
rf_reg_final.fit(X_train, y_train.ravel()) 
print('training accuracy (r_sq) is: ', rf_reg_final.score(X_train,y_train))
print('testing accuracy (r_sq) is: ', rf_reg_final.score(X_test,y_test))
print('training mse: ', mean_squared_error(rf_reg_final.predict(X_train), y_train))
print('testing mse: ', mean_squared_error(rf_reg_final.predict(X_test), y_test))
print('The testing MSE has improved by ', train_mean_squared_error_b4Tune-mean_squared_error(rf_reg_final.predict(X_train), y_train), 'after tuning.')
print('The testing MSE has improved by ', test_mean_squared_error_b4Tune-mean_squared_error(rf_reg_final.predict(X_test), y_test), 'after tuning.')

training accuracy (r_sq) is:  0.913436605858109
testing accuracy (r_sq) is:  0.8944416546519409
training mse:  1.8520349831091616
testing mse:  2.016348755379508
The testing MSE has improved by  1.9023668998911945 after tuning.
The testing MSE has improved by  1.196918211151203 after tuning.


<div style='color: #216969;
           background-color: #EAF6F6;
           font-size: 200%;
           border-radius:15px;
           text-align:center;
           font-weight:600;
           border-style: solid;
           border-color: dark green;
           padding: 1%;
           font-family: "Cambria";'>
(Final Model) K-Folds Cross Validation
<a class="anchor" id="1"></a> 

In [36]:
results  = cross_validate(rf_reg_final, dfX, dfy.ravel(), scoring='neg_mean_squared_error', cv=5, return_train_score = True)
print('cross val training mse:', sum(-results['train_score'])/len(results['train_score']))
print('cross val testing mse:', sum(-results['test_score'])/len(results['test_score']))

cross val training mse: 1.843692761102719
cross val testing mse: 3.231980154528808


In [37]:
pd.concat((pd.DataFrame(X_train.iloc[:, 0:].columns, columns = ['variable']), 
           pd.DataFrame(rf_reg_final.feature_importances_, columns = ['importance'])), 
          axis = 1).sort_values(by='importance', ascending = False)

variable  importance
31          G2    0.840163
29    absences    0.126513
2          age    0.016855
30          G1    0.002915
10      reason    0.002628
23      famrel    0.002333
27        Walc    0.001345
28      health    0.001130
14    failures    0.000974
25       goout    0.000653
9         Fjob    0.000651
22    romantic    0.000615
24    freetime    0.000450
8         Mjob    0.000435
7         Fedu    0.000358
26        Dalc    0.000331
12  traveltime    0.000260
11    guardian    0.000255
6         Medu    0.000250
17        paid    0.000233
18  activities    0.000194
1          sex    0.000159
16      famsup    0.000104
4      famsize    0.000060
19     nursery    0.000060
15   schoolsup    0.000038
13   studytime    0.000036
21    internet    0.000000
20      higher    0.000000
5      Pstatus    0.000000
3      address    0.000000
0       school    0.000000

In [38]:
#The statsmodel.api provides key summary statistics
#The lm2 model refers to statsmodel.api model
#Add a constant to the X_train dataset and rename it as X_train_sm
X_train_sm = sm.add_constant(X_train)
print(X_train_sm)
print(X_train_sm.shape)

#Create another model using statsmodel.api using the Ordinary Least Squares (OLS) method for the model
lm2 = sm.OLS(y_train, X_train_sm).fit()

lm2.summary()

     const  school  sex  age  address  famsize  Pstatus  Medu  Fedu  Mjob  \
278    1.0       0    0   18        1        1        1     4     4     1   
203    1.0       0    0   17        0        1        1     2     2     4   
339    1.0       0    0   17        0        1        0     3     2     4   
3      1.0       0    0   15        1        1        1     4     2     1   
262    1.0       0    1   18        0        1        1     3     2     4   
..     ...     ...  ...  ...      ...      ...      ...   ...   ...   ...   
299    1.0       0    1   18        1        0        1     4     4     3   
22     1.0       0    1   16        1        0        1     4     2     3   
72     1.0       0    0   15        0        1        1     1     1     4   
15     1.0       0    0   16        1        1        1     4     4     1   
168    1.0       0    0   16        1        1        1     2     2     4   

     ...  romantic  famrel  freetime  goout  Dalc  Walc  health  absences  

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                     G3   R-squared:                       0.841
Model:                            OLS   Adj. R-squared:                  0.823
Method:                 Least Squares   F-statistic:                     46.62
Date:                Mon, 07 Nov 2022   Prob (F-statistic):           3.57e-94
Time:                        20:29:19   Log-Likelihood:                -642.28
No. Observations:                 316   AIC:                             1351.
Df Residuals:                     283   BIC:                             1475.
Df Model:                          32                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         -0.8310      2.339     -0.355      0.723      -5.434       3.772
school         0.5874      0.411      1.428      0.154      -0.222       1.397
sex            0.0601      0.269      0.223      0.824      -0.470       0.590
age           -0.2280      0.111     -2.045      0.042      -0.447      -0.009
address        0.0287      0.318      0.090      0.928      -0.598       0.656
famsize       -0.1313      0.267     -0.491      0.624      -0.658       0.395
Pstatus        0.0163      0.371      0.044      0.965      -0.713       0.746
Medu           0.1141      0.142      0.805      0.421      -0.165       0.393
Fedu          -0.0181      0.142     -0.128      0.899      -0.297       0.261
Mjob           0.0203      0.084      0.241      0.810      -0.145       0.186
Fjob           0.0458      0.098      0.468      0.640      -0.147       0.238
reason         0.1049      0.122      0.860      0.391      -0.135       0.345
guardian      -0.2552      0.202     -1.263      0.208      -0.653       0.142
traveltime     0.1524      0.181      0.844      0.399      -0.203       0.508
studytime     -0.1084      0.155     -0.701      0.484      -0.413       0.196
failures       0.1959      0.197      0.996      0.320      -0.191       0.583
schoolsup      0.5267      0.362      1.455      0.147      -0.186       1.239
famsup         0.0787      0.258      0.305      0.760      -0.429       0.586
paid           0.1029      0.254      0.405      0.686      -0.398       0.603
activities    -0.3403      0.235     -1.450      0.148      -0.802       0.122
nursery       -0.5201      0.305     -1.706      0.089      -1.120       0.080
higher         0.2102      0.573      0.367      0.714      -0.918       1.339
internet      -0.0139      0.314     -0.044      0.965      -0.631       0.604
romantic      -0.2609      0.249     -1.046      0.297      -0.752       0.230
famrel         0.2994      0.129      2.324      0.021       0.046       0.553
freetime       0.0991      0.124      0.796      0.427      -0.146       0.344
goout          0.0105      0.125      0.084      0.933      -0.235       0.257
Dalc          -0.1645      0.185     -0.889      0.375      -0.528       0.200
Walc           0.1337      0.132      1.010      0.314      -0.127       0.394
health         0.0951      0.082      1.157      0.248      -0.067       0.257
absences       0.0421      0.014      2.923      0.004       0.014       0.070
G1             0.2158      0.067      3.206      0.002       0.083       0.348
G2             0.9571      0.057     16.725      0.000       0.844       1.070
==============================================================================
Omnibus:                      147.860   Durbin-Watson:                   1.895
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              639.642
Sk

[CV 3/5; 4139/4320] END bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=8, min_samples_split=7, n_estimators=50;, score=-8.033 total time=   0.0s
[CV 4/5; 4139/4320] START bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=8, min_samples_split=7, n_estimators=50
[CV 4/5; 4139/4320] END bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=8, min_samples_split=7, n_estimators=50;, score=-8.279 total time=   0.0s
[CV 5/5; 4139/4320] START bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=8, min_samples_split=7, n_estimators=50
[CV 5/5; 4139/4320] END bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=8, min_samples_split=7, n_estimators=50;, score=-6.023 total time=   0.0s
[CV 1/5; 4140/4320] START bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=8, min_samples_split=7, n_estimators=100
[CV 1/5; 4140/4320] END bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=8, min_samples

[CV 3/5; 3978/4320] END bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=8, min_samples_split=4, n_estimators=100;, score=-3.668 total time=   0.1s
[CV 2/5; 3996/4320] START bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=8, min_samples_split=7, n_estimators=100
[CV 2/5; 3996/4320] END bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=8, min_samples_split=7, n_estimators=100;, score=-2.826 total time=   0.1s
[CV 3/5; 3996/4320] START bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=8, min_samples_split=7, n_estimators=100
[CV 3/5; 3996/4320] END bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=8, min_samples_split=7, n_estimators=100;, score=-3.668 total time=   0.1s
[CV 4/5; 3996/4320] START bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=8, min_samples_split=7, n_estimators=100
[CV 4/5; 3996/4320] END bootstrap=False, max_depth=16, max_features=auto, min_samples_leaf=8, min_sa

[CV 3/5; 4166/4320] END bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=15, min_samples_split=6, n_estimators=30;, score=-8.894 total time=   0.0s
[CV 4/5; 4166/4320] START bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=15, min_samples_split=6, n_estimators=30
[CV 4/5; 4166/4320] END bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=15, min_samples_split=6, n_estimators=30;, score=-8.845 total time=   0.0s
[CV 5/5; 4166/4320] START bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=15, min_samples_split=6, n_estimators=30
[CV 5/5; 4166/4320] END bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=15, min_samples_split=6, n_estimators=30;, score=-6.560 total time=   0.0s
[CV 1/5; 4167/4320] START bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=15, min_samples_split=6, n_estimators=35
[CV 1/5; 4167/4320] END bootstrap=False, max_depth=16, max_features=sqrt, min_samples_leaf=15, min_s